In [1]:
import pandas as pd
import numpy as np
from darts import TimeSeries
from darts.models import RandomForest
from darts.models import XGBModel
from darts.models import Prophet
from darts.models import LightGBMModel
from sklearn.metrics import mean_squared_error, mean_squared_log_error

Importing plotly failed. Interactive plots will not work.
C:\Users\Usman.nazir\.conda\envs\pytorch_env\lib\site-packages\statsforecast\utils.py:237: FutureWarning: 'M' is deprecated and will be removed in a future version, please use 'ME' instead.
  "ds": pd.date_range(start="1949-01-01", periods=len(AirPassengers), freq="M"),


In [2]:
df = pd.read_csv("train_darts_univariate.csv", parse_dates=["date"])

In [3]:
df.head()

date  store_nbr  family  sales
0 2013-01-01          1       0    0.0
1 2013-01-01          1       1    0.0
2 2013-01-01          1       2    0.0
3 2013-01-01          1       3    0.0
4 2013-01-01          1       4    0.0

In [4]:
unique_combinations = df[['store_nbr', 'family']].drop_duplicates()

In [5]:
total_rmse = 0
total_rmsle = 0
num_models = 0

In [6]:
trained_models_rf = {}
trained_models_xgb = {}
trained_models_p = {}
trained_models_lgbm = {}

In [7]:
for index, row in unique_combinations.iterrows():
    store_nbr = row['store_nbr']
    family = row['family']
    
    print(f"\nTraining model for store {store_nbr} and family {family}...")
    
    df_subset = df[(df['store_nbr'] == store_nbr) & (df['family'] == family)]
    
    df_subset_p = df_subset.copy()
    
    df_subset_p.set_index('date', inplace=True)
    
    ts = TimeSeries.from_dataframe(df_subset, value_cols=["sales"])
    
    ts_p = TimeSeries.from_dataframe(df_subset_p, value_cols=["sales"], freq='d')

    split_ratio = 0.8
    training_size = int(len(ts) * split_ratio)
    
    train = ts[:training_size]
    train_p = ts_p[:training_size]
    
    val = ts[training_size:]
    val_p = ts_p[training_size:]
    
    model_rf = RandomForest(lags=2)
    model_xgb = XGBModel(lags=2)
    model_p = Prophet()
    model_lgbm = LightGBMModel(lags=2)
    
    model_rf.fit(train)
    model_xgb.fit(train)
    model_p.fit(train_p)
    model_lgbm.fit(train)

    trained_models_rf[(store_nbr, family)] = model_rf
    trained_models_xgb[(store_nbr, family)] = model_xgb
    trained_models_p[(store_nbr, family)] = model_p
    trained_models_lgbm[(store_nbr, family)] = model_lgbm

    predictions_rf = model_rf.predict(n=len(val))
    predictions_xgb = model_xgb.predict(n=len(val))
    predictions_p = model_p.predict(n=len(val_p))
    predictions_lgbm = model_lgbm.predict(n=len(val))

    val = val.pd_series().tolist()
    val_p = val_p.pd_series().tolist()
    
    predictions_rf = predictions_rf.pd_series().tolist()
    predictions_xgb = predictions_xgb.pd_series().tolist()
    predictions_p = predictions_p.pd_series().tolist()
    predictions_lgbm = predictions_lgbm.pd_series().tolist()

    predictions_rf = np.maximum(predictions_rf, 0)
    predictions_xgb = np.maximum(predictions_xgb, 0)
    predictions_p = np.maximum(predictions_p, 0)
    predictions_lgbm = np.maximum(predictions_lgbm, 0)
    
    nan_indices = np.isnan(val_p)
    nan_count = np.sum(nan_indices)
    
    if nan_count > 0:
        print(f"There are {nan_count} NaN values in the data.")
        
    val_p = np.nan_to_num(val_p, nan=0.0)

    rmse_rf = np.sqrt(mean_squared_error(val, predictions_rf))
    rmsle_rf = np.sqrt(mean_squared_error(np.log1p(val), np.log1p(predictions_rf)))
    
    rmse_xgb = np.sqrt(mean_squared_error(val, predictions_xgb))
    rmsle_xgb = np.sqrt(mean_squared_error(np.log1p(val), np.log1p(predictions_xgb)))
    
    rmse_p = np.sqrt(mean_squared_error(val_p, predictions_p))
    rmsle_p = np.sqrt(mean_squared_error(np.log1p(val_p), np.log1p(predictions_p)))
    
    rmse_lgbm = np.sqrt(mean_squared_error(val, predictions_lgbm))
    rmsle_lgbm = np.sqrt(mean_squared_error(np.log1p(val), np.log1p(predictions_lgbm)))
    
    rmse = min(rmse_rf, rmse_xgb, rmse_p, rmse_lgbm)
    rmsle = min(rmsle_rf, rmsle_xgb, rmse_p, rmsle_lgbm)

    total_rmse += rmse
    total_rmsle += rmsle
    num_models += 1

    print(f"Root Mean Squared Error (RMSE): {rmse}")
    print(f"Root Mean Squared Logarithmic Error (RMSLE): {rmsle}")


Training model for store 1 and family 0...


19:03:20 - cmdstanpy - INFO - Chain [1] start processing
19:03:21 - cmdstanpy - INFO - Chain [1] done processing


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000169 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 30
[LightGBM] [Info] Number of data points in the train set: 1345, number of used features: 2
[LightGBM] [Info] Start training from score 3.064684
There are 1 NaN values in the data.
Root Mean Squared Error (RMSE): 2.8591550287823453
Root Mean Squared Logarithmic Error (RMSLE): 0.600926499233728

Training model for store 1 and family 1...
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 1345, number of used features: 0
[LightGBM] [Warning] Stopped training because there are no more 

19:03:28 - cmdstanpy - INFO - Chain [1] start processing
19:03:28 - cmdstanpy - INFO - Chain [1] done processing


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000133 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 20
[LightGBM] [Info] Number of data points in the train set: 1345, number of used features: 2
[LightGBM] [Info] Start training from score 2.171747
There are 1 NaN values in the data.
Root Mean Squared Error (RMSE): 2.334948444399842
Root Mean Squared Logarithmic Error (RMSLE): 0.5794103107014754

Training model for store 1 and family 3...


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000397 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 454
[LightGBM] [Info] Number of data points in the train set: 1345, number of used features: 2
[LightGBM] [Info] Start training from score 789.004433
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

20:51:32 - cmdstanpy - INFO - Chain [1] start processing
20:51:32 - cmdstanpy - INFO - Chain [1] done processing


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000418 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 69
[LightGBM] [Info] Number of data points in the train set: 1345, number of used features: 2
[LightGBM] [Info] Start training from score 5.108550
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, bes

20:51:36 - cmdstanpy - INFO - Chain [1] start processing
20:51:36 - cmdstanpy - INFO - Chain [1] done processing


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000393 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 510
[LightGBM] [Info] Number of data points in the train set: 1345, number of used features: 2
[LightGBM] [Info] Start training from score 16.850067
There are 1 NaN values in the data.
Root Mean Squared Error (RMSE): 9.139458190411824
Root Mean Squared Logarithmic Error (RMSLE): 0.628014495703557


In [8]:
avg_rmse = total_rmse / num_models
avg_rmsle = total_rmsle / num_models

In [9]:
print(f"Average Root Mean Squared Error (RMSE) across all models: {avg_rmse}")
print(f"Average Root Mean Squared Logarithmic Error (RMSLE) across all models: {avg_rmsle}")

Average Root Mean Squared Error (RMSE) across all models: 159.49358307169695
Average Root Mean Squared Logarithmic Error (RMSLE) across all models: 0.6592078065208438
